In [1]:
import mwu_measures
import pandas as pd
import numpy as np
import mwu_measures.processing_corpus
from mwu_measures.corpus_helper import Fetcher

mwu_examples = pd.read_csv('MultiwordExpression_Concreteness_Ratings.csv')
mwu_examples['length'] = mwu_examples['Expression'].apply(lambda x: len(x.split()))
mwu_examples = mwu_examples.loc[(mwu_examples['length'] == 2) | (mwu_examples['length'] == 3)]
mwu_examples['Expression'] = mwu_examples['Expression'].apply(lambda x: x.lower())
this_corpus = mwu_measures.processing_corpus.process_corpus('bnc', 'small_corpus.txt', chunk_size=10000000, verbose=True)
ngram_selection = mwu_examples['Expression'].tolist()
# ngram_selection = [ngram.split() for ngram in ngram_selection]
# ngram_chunks = np.array_split(ngram_selection, 100)

90357 lines processed
178289 lines processed
287795 lines processed
301046 lines processed
we bring the boom


In [2]:
helper = Fetcher(this_corpus.corpus_conn)

In [4]:
helper.fetch_scores('ug_2', 'ug_1', helper.fetch_bigrams(ngram_selection, 'bw'), 'bigram')

{'bio lab': {'C': {'group': 1.0},
  'G': {'biology': 1.0, 'the': 1.0, 'police': 1.0, 'avr': 1.0, 'met': 1.0},
  'J': {'xrays': 1.0, 'of': 1.0, 'the': 1.0},
  'H': {'arts': 2.0, 'the': 1.0},
  'K': {'a': 1.0,
   'robinson': 1.0,
   'williams': 1.0,
   'science': 1.0,
   'the': 1.0,
   'mp': 1.0},
  'A': {'arts': 2.0, 'processing': 1.0, 'the': 1.0},
  'F': {'the': 1.0, 'any': 1.0, 'his': 1.0, 'as': 1.0, 'in': 1.0},
  'B': {'of': 1.0, 'biotech': 1.0, 'the': 1.0}},
 'record label': {'E': {'and': 1.0,
   'a': 1.0,
   'partofspeech': 1.0,
   'french': 1.0,
   'readytowear': 1.0},
  'F': {'the': 2.0,
   'a': 2.0,
   'to': 2.0,
   'may': 1.0,
   'independent': 1.0,
   'verbal': 1.0,
   'just': 1.0,
   'could': 1.0,
   'prescription': 1.0},
  'A': {'the': 3.0,
   'same': 1.0,
   'indie': 1.0,
   'address': 1.0,
   'eurobeer': 1.0,
   'better': 1.0,
   'unfairly': 1.0,
   'different': 1.0,
   'warning': 1.0},
  'J': {'green': 1.0, 'such': 1.0, 'the': 1.0, 'black': 1.0},
  'B': {'midprice': 1.0,


In [4]:
helper.conn.execute("SELECT * FROM trigram_db LIMIT 100").fetch_df()

corpus    ug_1      ug_2     ug_3            big_1  freq
0       A   $1.70        he  reckons         $1.70 he   1.0
1       A   $1.80        on        a         $1.80 on   1.0
2       A   $1.80        or       as         $1.80 or   1.0
3       A  $17.5m  american  express  $17.5m american   1.0
4       A      $2         a     time             $2 a   1.0
..    ...     ...       ...      ...              ...   ...
95      A       (     laugh      but          ( laugh   1.0
96      A       (    lionel   jospin         ( lionel   1.0
97      A       (      lone  snigger           ( lone   1.0
98      A       (      look       at           ( look   1.0
99      A       (      look     good           ( look   1.0

[100 rows x 6 columns]

In [3]:
# x = helper.fetch_bigrams(ngram_selection, 'bw') # BIgRAM IS OK

In [8]:
trigrams = [[' '.join(ngram), ' '.join([ngram[0], ngram[1]])] for ngram in ngram_selection if len(ngram) == 3]
# trigrams = [[' '.join(ngram), ngram[2]] for ngram in ngram_selection if len(ngram) == 3]

In [10]:
trigrams = pd.DataFrame(trigrams, columns = ['query', 'big_1'])
# trigrams = pd.DataFrame(trigrams, columns = ['query', 'ug_3'])

In [11]:
trigrams

query      big_1
0     ‘tis the season   ‘tis the
1         8 ball pool     8 ball
2         a bad break      a bad
3           a big ask      a big
4          a big deal      a big
...               ...        ...
9722    zest for life   zest for
9723    zip one's lip  zip one's
9724     zip your lip   zip your
9725       zone in on    zone in
9726       zoom in on    zoom in

[9727 rows x 2 columns]

In [12]:
this_corpus.corpus_conn.execute(
    """
    CREATE OR REPLACE TEMPORARY TABLE this_query (query TEXT, big_1 TEXT, hash_index UINT64)
""")
this_corpus.corpus_conn.execute(f"""
    INSERT INTO this_query SELECT *, hash(big_1) AS hash_index FROM trigrams
""")

In [12]:
this_corpus.corpus_conn.execute(
    """
    CREATE OR REPLACE TEMPORARY TABLE this_query (query TEXT, ug_3 TEXT, hash_index UINT64)
""")
this_corpus.corpus_conn.execute(f"""
    INSERT INTO this_query SELECT *, hash(ug_3) AS hash_index FROM trigrams
""")

In [13]:
this_corpus.corpus_conn.execute("SELECT * FROM this_query").fetch_df()

query      big_1            hash_index
0     ‘tis the season   ‘tis the    367049523107210819
1         8 ball pool     8 ball  13478181352906029041
2         a bad break      a bad   3783471393295332674
3           a big ask      a big   3347211066445533376
4          a big deal      a big   3347211066445533376
...               ...        ...                   ...
9722    zest for life   zest for  12779792370419524593
9723    zip one's lip  zip one's   1131825406419085369
9724     zip your lip   zip your   1021777779954715733
9725       zone in on    zone in   9675242506793349944
9726       zoom in on    zoom in  17964358105306547001

[9727 rows x 3 columns]

In [7]:
f"""
            CREATE OR REPLACE TABLE joined_db AS                  
            SELECT 
                query,
                corpus,
                ug_1,
                ug_2,
                """
f"""SUM(freq) as freq
            FROM this_query
            INNER JOIN filtered_db
            USING(hash_index)
            GROUP BY
                query,
                corpus,
                ug_1,
                ug_2
            ORDER BY ug_3, freq DESC
        """

'SUM(freq) as freq\n            FROM this_query\n            INNER JOIN filtered_db\n            USING(hash_index)\n            GROUP BY\n                query,\n                corpus,\n                ug_1,\n                ug_2\n            ORDER BY ug_3, freq DESC\n        '

In [14]:
this_corpus.corpus_conn.execute(
    f"""
    CREATE OR REPLACE TABLE filtered_db AS
    SELECT
        corpus,
        hash(big_1) as hash_index,
        ug_3,
        freq
    FROM trigram_db
    WHERE 
        hash_index IN (
            SELECT hash_index FROM this_query
        )
""")
# this_corpus.corpus_conn.execute(
#     f"""
#     CREATE OR REPLACE TABLE filtered_db AS
#     SELECT
#         corpus,
#         hash(ug_3) as hash_index,
#         ug_1,
#         ug_2,
#         freq
#     FROM trigram_db
#     WHERE 
#         hash_index IN (
#             SELECT hash_index FROM this_query
#         )
# """)

In [15]:
this_corpus.corpus_conn.execute("SELECT * FROM filtered_db").fetch_df()

corpus            hash_index        ug_3  freq
0           A  10906082780163188628          be  22.0
1           A  10906082780163188628  constitute   1.0
2           A  10906082780163188628        date   1.0
3           A  10906082780163188628      depend   1.0
4           A  10906082780163188628        give   1.0
...       ...                   ...         ...   ...
311467      H  12661906849691086516         7:2   1.0
311468      H  12661906849691086516  confidence   6.0
311469      H  12661906849691086516       equal   1.0
311470      H  12661906849691086516          no   5.0
311471      H  12661906849691086516         the   2.0

[311472 rows x 4 columns]

In [71]:
# this_corpus.corpus_conn.execute("SELECT * FROM filtered_db WHERE hash_1 = hash('a') AND hash_2 = hash('number') AND ug_3 = 'of'").fetch_df()

corpus              hash_1              hash_2 ug_3   freq
0      D  584566915021039271  180176074552245289   of    1.0
1      E  584566915021039271  180176074552245289   of   76.0
2      A  584566915021039271  180176074552245289   of   91.0
3      G  584566915021039271  180176074552245289   of   71.0
4      B  584566915021039271  180176074552245289   of   58.0
5      F  584566915021039271  180176074552245289   of   89.0
6      J  584566915021039271  180176074552245289   of   35.0
7      C  584566915021039271  180176074552245289   of  115.0
8      H  584566915021039271  180176074552245289   of  199.0
9      K  584566915021039271  180176074552245289   of   53.0

In [16]:
this_corpus.corpus_conn.execute(
    f"""
    CREATE OR REPLACE TABLE joined_db AS                  
    SELECT 
        query,
        corpus,
        this_query.big_1,
        filtered_db.ug_3,
        freq
    FROM this_query
    INNER JOIN filtered_db
    USING(hash_index)
""")

# this_corpus.corpus_conn.execute(
#     f"""
#     CREATE OR REPLACE TABLE joined_db AS                  
#     SELECT 
#         query,
#         corpus,
#         filtered_db.ug_1,
#         filtered_db.ug_2,
#         this_query.ug_3,
#         freq
#     FROM this_query
#     INNER JOIN filtered_db
#     USING(hash_index)
# """)

In [17]:
this_corpus.corpus_conn.execute("SELECT * FROM joined_db ORDER BY freq DESC LIMIT 100").fetch_df()

query corpus     big_1  ug_3   freq
0   i don't understand      K   i don't  know  252.0
1         i don't know      K   i don't  know  252.0
2         i don't care      K   i don't  know  252.0
3             a lot of      K     a lot    of  199.0
4          a number of      H  a number    of  199.0
..                 ...    ...       ...   ...    ...
95        out of sight      C    out of   the  146.0
96        out of shape      C    out of   the  146.0
97       out of season      C    out of   the  146.0
98        out of reach      C    out of   the  146.0
99        out of range      C    out of   the  146.0

[100 rows x 5 columns]